# 2회 기출 변형

- 작업 3유형 통계 반영

```
광고 한번 눌러주라
```

# 작업 1유형

```{attention} 
데이터설명 : 보스턴집값, 각 행은 지역구별 집값관련된 메타정보 : https://www.kaggle.com/datasets/arunjathari/bostonhousepricedata   
**DataUrl = https://raw.githubusercontent.com/Datamanim/datarepo/main/krdatacertificate/e2_p1_1.csv**
```

In [1]:
import pandas as pd
df = pd.read_csv('https://raw.githubusercontent.com/Datamanim/datarepo/main/krdatacertificate/e2_p1_1.csv')
df.head(2)

CRIM  ZN  INDUS  CHAS    NOX     RM   AGE     DIS  RAD    TAX  PTRATIO  \
0  0.00632 NaN   2.31     0  0.538  6.575  65.2  4.0900    1  296.0     15.3   
1  0.02731 NaN   7.07     0  0.469  6.421  78.9  4.9671    2  242.0     17.8   

       B  LSTAT  MEDV  
0  396.9   4.98  24.0  
1  396.9   9.14  21.6

```{admonition} 1-1
주어진 Dataset에서 CRIM값이 가장 큰 10개의 지역을 구하고     
10개의 지역의 CRIM값을 그 중 가장 작은 값으로 대체하라. 그리고          
AGE 컬럼 값이 80이상인 대체 된 CRIM 평균값을 구하라      
```

In [2]:
df =df.sort_values('CRIM',ascending=False).reset_index(drop=True)
df.loc[:9,'CRIM'] = df.loc[:9,'CRIM'].min()
mean = df[df.AGE >=80].CRIM.mean()
print(mean)

5.759386625


```{admonition} 1-2
**1-1에서 사용한 데이터에서 RM 중앙값으로 해당 컬럼의 결측치를 대체하라          
그리고 해당 컬럼의 결측치 대치 전후의 표준편차 차이의 절댓값을 소숫점 이하 3째자리 까지 구하라**
```

In [16]:
import numpy as np

pre_std = df.RM.std()
df.RM = df.RM.fillna(df.RM.median())
after_std = df.RM.std()

result = abs(round(after_std - pre_std,3))
print(result)

0.027


```{admonition} 1-3
**주어진 Dataset의 DIS 평균으로 부터 1.5 * 표준편차를 벗어나는 영역을 이상치라고 판단하고     
DIS 컬럼의 이상치들의 합을 구하여라.**
```

In [24]:
result = df[(df.DIS > df.DIS.mean() + 1.5 * df.DIS.std()) | (df.DIS < df.DIS.mean() - 1.5 * df.DIS.std())].DIS.sum()
print(result)

404.4101


# 작업 2유형

```{attention}  
데이터 설명 : e-commerce 배송의 정시 도착여부 (1: 정시배송 0 : 정시미배송)    
x_train: https://raw.githubusercontent.com/Datamanim/datarepo/main/shipping/X_train.csv    
y_train: https://raw.githubusercontent.com/Datamanim/datarepo/main/shipping/y_train.csv  
x_test: https://raw.githubusercontent.com/Datamanim/datarepo/main/shipping/X_test.csv    
x_label(평가용) : https://raw.githubusercontent.com/Datamanim/datarepo/main/shipping/y_test.csv    
데이터 출처 :https://www.kaggle.com/datasets/prachi13/customer-analytics (참고, 데이터 수정)       

**x_train 데이터로 학습한 모델을 x_test에 적용하여 예측한 결과를 제출하라. 평가 지표는 f1_score이다.**
```  

In [1]:
import pandas as pd
#데이터 로드
x_train = pd.read_csv("https://raw.githubusercontent.com/Datamanim/datarepo/main/shipping/X_train.csv")
y_train = pd.read_csv("https://raw.githubusercontent.com/Datamanim/datarepo/main/shipping/y_train.csv")
x_test= pd.read_csv("https://raw.githubusercontent.com/Datamanim/datarepo/main/shipping/X_test.csv")


display(x_train.head())
display(y_train.head())

ID Warehouse_block Mode_of_Shipment Customer_care_calls  Customer_rating  \
0  6045               A           Flight                   4                3   
1    44               F             Ship                   3                1   
2  7940               F             Road                   4                1   
3  1596               F             Ship                   4                3   
4  4395               A           Flight                   5                3   

   Cost_of_the_Product  Prior_purchases Product_importance Gender  \
0                  266                5               high      F   
1                  174                2                low      M   
2                  154               10               high      M   
3                  158                3             medium      F   
4                  175                3                low      M   

   Discount_offered  Weight_in_gms  
0                 5           1590  
1                44           1556  
2                10           5674  
3                27           1207  
4                 7           4833

ID  Reached.on.Time_Y.N
0  6045                    0
1    44                    1
2  7940                    1
3  1596                    1
4  4395                    1

In [26]:
# print(x_train.info())
# print(x_train.nunique())
# print(x_train.isnull().sum())
# 결측치가 있지만 따로 처리하지 않고 더미화


# 범주형 변수인데 적당히 많은 unique값을 가진 컬럼은 날린다.
drop_col = ['ID']
x_train_drop = x_train.drop(columns = drop_col)
x_test_drop = x_test.drop(columns = drop_col)

# import sklearn
# print(sklearn.__all__)
# import sklearn.model_selection
# print(dir(sklearn.model_selection))

from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
x_train_dummies = pd.get_dummies(x_train_drop)
y = y_train['Reached.on.Time_Y.N']


x_test_dummies = pd.get_dummies(x_test_drop)
# train과 컬럼 순서 동일하게 하기 (더미화 하면서 순서대로 정렬을 이미 하기 때문에 오류가 난다면 해당 컬럼이 누락된것)
x_test_dummies = x_test_dummies[x_train_dummies.columns]
# print(help(train_test_split))



X_train, X_validation, Y_train, Y_validation = train_test_split(x_train_dummies, y, test_size=0.33, random_state=42)
rf = RandomForestClassifier(random_state =23)
rf.fit(X_train,Y_train)

# import sklearn.metrics
# print(dir(sklearn.metrics))

from sklearn.metrics import accuracy_score , f1_score, recall_score, roc_auc_score ,precision_score

#model_score
predict_train_label = rf.predict(X_train)
predict_train_proba = rf.predict_proba(X_train)[:,1]

predict_validation_label = rf.predict(X_validation)
predict_validation_prob = rf.predict_proba(X_validation)[:,1]


# 문제에서 묻는 것에 따라 모델 성능 확인하기
# 정확도 (accuracy) , f1_score , recall , precision -> model.predict로 결과뽑기
# auc , 확률이라는 표현있으면 model.predict_proba로 결과뽑고 첫번째 행의 값을 가져오기 model.predict_proba()[:,1]
print('train accuracy :', accuracy_score(Y_train,predict_train_label))
print('validation accuracy :', accuracy_score(Y_validation,predict_validation_label))
print('\n')
print('train f1_score :', f1_score(Y_train,predict_train_label))
print('validation f1_score :', f1_score(Y_validation,predict_validation_label))
print('\n')
print('train recall_score :', recall_score(Y_train,predict_train_label))
print('validation recall_score :', recall_score(Y_validation,predict_validation_label))
print('\n')
print('train precision_score :', precision_score(Y_train,predict_train_label))
print('validation precision_score :', precision_score(Y_validation,predict_validation_label))
print('\n')
print('train auc :', roc_auc_score(Y_train,predict_train_proba))
print('validation auc :', roc_auc_score(Y_validation,predict_validation_prob))


# test데이터 마찬가지 위와 같은 방식
predict_test_label = rf.predict(x_test_dummies)
predict_test_proba = rf.predict_proba(x_test_dummies)[:,1]


# accuracy, f1_score, recall, precision 
#pd.DataFrame({'ID': x_test.ID, 'Reached.on.Time_Y.N': predict_test_label}).to_csv('003000000.csv', index=False)

# auc, 확률
#pd.DataFrame({'ID': x_test.ID, 'Reached.on.Time_Y.N': predict_test_proba}).to_csv('003000000.csv', index=False)

train accuracy : 1.0
validation accuracy : 0.6395775941230487


train f1_score : 1.0
validation f1_score : 0.6744089589382


train recall_score : 1.0
validation recall_score : 0.630721489526765


train precision_score : 1.0
validation precision_score : 0.7245989304812834


train auc : 1.0
validation auc : 0.7261997118475008


# 작업 3유형

```{attention} 
어느 호수에서 잡은 물고기 122마리 길이 데이터(자체제작)
**DataUrl = https://raw.githubusercontent.com/Datamanim/datarepo/main/krdatacertificate/e2_p3_1.csv**
```

In [34]:
import pandas as pd
df = pd.read_csv('https://raw.githubusercontent.com/Datamanim/datarepo/main/krdatacertificate/e2_p3_1.csv')
df.head(5)

fish   height
0  fish_1  33.74cm
1  fish_2  31.64cm
2  fish_3  27.49cm
3  fish_4  31.43cm
4  fish_5  27.56cm

```{admonition} 3-1-a
**122마리의 height 평균값을 m(미터) 단위로 소숫점 이하 5자리까지 실수 값만 출력하라**
```

In [35]:
df['height_raw'] =df['height'].str.replace('cm','').astype('float')
result = round(df['height_raw'].mean()/100,5)
result

0.29951

```{admonition} 3-1-b
**모집단의 평균 길이가 30cm 인지 확인하려 일표본 t 검정을 시행하여 확인하려한다. 검정통계량을 소숫점 이하 3째자리까지 구하여라**
```

In [38]:
from scipy.stats import ttest_1samp

s ,p = ttest_1samp(df['height_raw'],30)
result = round(s,3)
print(result)

-0.217


```{admonition} 3-1-c
**위의 통계량에 대한 p-값을 구하고 (반올림하여 소숫점 이하 3째자리), 유의수준 0.05하에서 귀무가설과 대립가설중 유의한 가설을 하나를 선택하시오(귀무/대립)**
```

In [42]:
p_result =round(p,3)
result = '귀무'
print(p_result)
print(result)

0.829
귀무


```{attention} 
조사결과 70%의 성인 남성이 3년 동안에 적어도 1번 치과를 찾는다고 할때, 21명의 성인 남성이 임의로 추출되었다고 하자. 
```

```{admonition} 3-2 - a
**21명 중 16명 미만이 치과를 찾았을 확률(반올림하여 소숫점 이하 3자리)**
```

In [3]:
from scipy.stats import binom

n = 21
p = 0.7
k = 16

# P(X < k) 계산
prob = binom.cdf(k-1, n, p)
print(round(prob, 3))

0.637


```{admonition} 3-2 - b
**적어도 19명이 치과를 찾았을 확률(반올림하여 소숫점 이하 3자리)**
```

In [4]:
from scipy.stats import binom

n = 21
p = 0.7
k = 19

# P(X >= k) 계산
prob = 1 - binom.cdf(k-1, n, p)
print(round(prob, 3))

0.027
